In [159]:
import numpy as np
import matplotlib.pyplot as plt

In [160]:
#note, this function expects a matrix A[ix,iy] 
#and then displays so that A[:,0] is the lowest row of pixels
def display(A):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]

    #%matplotlib osx 

    plt.imshow(B); 
    plt.axis('off'); 
    plt.show()
    plt.draw()
    plt.pause(0.01)

In [161]:
mossParticles = 3200
maxX = 400
maxY = 80

In [162]:
mossMatrix = np.zeros((maxX, maxY))

# Introduce a sticky wall at the bottom by filling the lowest row of pixels with particles
mossMatrix[:,0] = 1
mossMatrix[:, maxY - 1] = 1
mossMatrix

array([[1., 0., 0., ..., 0., 0., 1.],
       [1., 0., 0., ..., 0., 0., 1.],
       [1., 0., 0., ..., 0., 0., 1.],
       ...,
       [1., 0., 0., ..., 0., 0., 1.],
       [1., 0., 0., ..., 0., 0., 1.],
       [1., 0., 0., ..., 0., 0., 1.]])

In [163]:
from numpy import random
randomLevels = random.randint(300, 600, size=(maxX // 4))

# Create a layer of nutrients that has different concentrations of nutrients every
# 4 units of length
nutrientLevels = np.array([])
for num in randomLevels:
    segment = np.array([num, num, num, num])
    nutrientLevels = np.concatenate((nutrientLevels, segment))
    
nutrientLevels

array([440., 440., 440., 440., 440., 440., 440., 440., 397., 397., 397.,
       397., 313., 313., 313., 313., 496., 496., 496., 496., 413., 413.,
       413., 413., 465., 465., 465., 465., 536., 536., 536., 536., 380.,
       380., 380., 380., 353., 353., 353., 353., 554., 554., 554., 554.,
       531., 531., 531., 531., 478., 478., 478., 478., 572., 572., 572.,
       572., 363., 363., 363., 363., 567., 567., 567., 567., 317., 317.,
       317., 317., 363., 363., 363., 363., 407., 407., 407., 407., 375.,
       375., 375., 375., 319., 319., 319., 319., 591., 591., 591., 591.,
       526., 526., 526., 526., 341., 341., 341., 341., 587., 587., 587.,
       587., 488., 488., 488., 488., 536., 536., 536., 536., 521., 521.,
       521., 521., 588., 588., 588., 588., 320., 320., 320., 320., 404.,
       404., 404., 404., 451., 451., 451., 451., 428., 428., 428., 428.,
       334., 334., 334., 334., 430., 430., 430., 430., 305., 305., 305.,
       305., 494., 494., 494., 494., 342., 342., 34

In [164]:
#test the display routine
display(mossMatrix)

In [165]:
# given the coordinate of a moss particle (or would-be moss particle),
# identify its root at the base of the mossMatrix.
def findRoot(x, y):
    path = [[x, y]]
    
    while y != 0:
        # Calculate all neighboring coordinates
        xp = x + 1
        if xp >= maxX:
            xp = maxX - xp
        xm = x - 1
        if xm < 0:
            xm = maxX + xm
        yp = y + 1
        if yp >= maxY:
            yp = maxY - yp
        ym = y - 1
        if ym < 0:
            ym = maxY + ym
            
        if mossMatrix[x, ym] == 1 and [x, ym] not in path:
            path.append([x, ym])
            y = ym
        elif mossMatrix[xp, y] == 1 and [xp, y] not in path:
            path.append([xp, y])
            x = xp
        elif mossMatrix[xm, y] == 1 and [xm, y] not in path:
            path.append([xm, y])
            x = xm
        elif mossMatrix[x, yp] == 1 and [x, yp] not in path:
            path.append([x, yp])
            y = yp
        else:
            # Stranded moss particles, abort
            break
            
    return x, path

In [166]:
yBuffer = 5
yStart  = 20
stickingProb = 0.15

In [167]:
for i in range(0,mossParticles):
    # Compute new starting point on the line y=yStart
    x  = np.random.randint(0,maxX)
    y  = yStart; #always start at upper limit

    while True:
        xOrg = x
        yOrg = y

        r = np.random.random(); # Random float:  0.0 <= r < 1.0
        #based on the value of 'r', move the particle
        #left, right, up, or down and change x and y accordingly
        if r <= 0.25:
            y = y + 1
        elif r <= 0.5:
            y = y - 1
        elif r <= 0.75:
            x = x + 1
        else:
            x = x - 1

        #now apply periodic boundary conditions to 'x'
        if x < 0:
            x = maxX + x
        elif x >= maxX:
            x = maxX - x

        if (mossMatrix[x,y] == 1 or y>yStart): 
            x = xOrg
            y = yOrg
            continue; # if this site has been taken try moving in a different direction

        #determine the x coordionates of the left and right neighbors
        #store them in 'xm' and 'xp' and apply periodic boundary conditions again
        xp = x + 1
        if xp >= maxX:
            xp = maxX - xp
        xm = x - 1
        if xm < 0:
            xm = maxX + xm
        yp = y + 1
        if yp >= maxY:
            yp = maxY - yp
        ym = y - 1
        if ym < 0:
            ym = maxY + ym

        # counting the number of filled neighbors
        n = int(mossMatrix[xp, y] == 1) + int(mossMatrix[xm, y] == 1)
        + int(mossMatrix[x, yp] == 1) + int(mossMatrix[x, ym] == 1)
        currStickingProb = stickingProb
        if n >= 2:
            currStickingProb = 1                                                      

        sticking_p = np.random.random()
        if sticking_p < currStickingProb:
            # Determine if any neighboring site is occupied
            # if that is the case, enter the following 'if' clause
            if (mossMatrix[xp, y] == 1 or mossMatrix[xm, y] == 1
                or mossMatrix[x, yp] == 1 or mossMatrix[x, ym] == 1):
                # Calculate the depletion of nutrients. The depletion increases
                # based on the height of the moss particle. The higher the particle is
                # (i.e. the bigger the moss is), the depletion increases.
                depletion = 1 + y
                # Try to find the root that this moss particle belongs to
                x_pos, path = findRoot(x, y)
                nutrientLevels[x_pos] = max(0, nutrientLevels[x_pos] - depletion)
                if (nutrientLevels[x_pos] > 0):
                    mossMatrix[x,y] = 1
                else:
                    # Since there are no more nutrients, remove the dead moss.
                    for coord in path:
                        mossMatrix[coord[0], coord[1]] = 0

                if (y+yBuffer>yStart and y+yBuffer<maxY): 
                    yStart = y+yBuffer

                if (i%400==0): 
                    print(f'i= {i} \tx={x} \ty={y} \tyStart={yStart}')
                    print("Available nutrients:", sum(nutrientLevels))

                nNewParticlesPerFrame = 400 
                if (i%nNewParticlesPerFrame==0):
                    display(mossMatrix)

                break # particle was attached, break out of current loop and insert next one

    if (yStart+1==maxY): 
        print(f'Structures reached Y limit after only {i} particles')
        break

display(mossMatrix)

i= 0 	x=221 	y=1 	yStart=20
Available nutrients: 178178.0
i= 400 	x=39 	y=1 	yStart=20
Available nutrients: 177024.0
i= 800 	x=68 	y=5 	yStart=20
Available nutrients: 175088.0
i= 1200 	x=214 	y=7 	yStart=20
Available nutrients: 172233.0
i= 1600 	x=91 	y=8 	yStart=25
Available nutrients: 168244.0
i= 2000 	x=367 	y=12 	yStart=26
Available nutrients: 163323.0
i= 2400 	x=112 	y=17 	yStart=31
Available nutrients: 157568.0
i= 2800 	x=270 	y=13 	yStart=33
Available nutrients: 150906.0


In [ ]:
mossMatrix

In [158]:
nutrientLevels

array([484., 550., 261., 548., 438., 381., 427., 440., 463., 423., 465.,
       165., 409., 138., 119.,   3., 540., 540., 503., 523., 363., 358.,
       363., 363., 425., 460., 412., 360., 379., 382., 100.,  92.,   0.,
       467.,  45., 381.,   0., 156., 294., 328., 429., 429., 378., 429.,
       388., 393., 238., 393., 320., 230., 320., 317., 399., 322.,   0.,
       399., 402.,   0., 355.,   0., 449., 230., 108., 387., 253., 239.,
       416., 416., 562., 470., 544., 555., 480., 485., 429., 483., 210.,
       410., 410., 408., 360., 380., 382., 360., 400., 400., 395.,  22.,
       362., 362., 344., 328.,   0., 230.,   0., 331.,   0., 171., 267.,
       424., 594., 594., 574., 594., 550., 509., 550., 548.,  91., 371.,
       368., 373., 436., 434., 491., 464., 424., 429., 417., 197., 476.,
       436., 481.,   0., 449., 484., 496., 493., 300.,  76., 295., 300.,
         0., 465., 410., 298.,   0.,  47., 202., 244., 307., 262., 288.,
       309., 399., 427., 424., 415., 359., 354., 36